[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/hammad-ali1/vad_clip_colab_notebook/blob/main/vadclip_feature_extraction.ipynb)

In [ ]:
!pip -q install ftfy
!pip -q install torch==2.4.0 torchvision==0.19.0 torchaudio==2.4.0
!pip -q install causal-conv1d==1.4.0 && pip install mamba-ssm==2.2.2
!pip -q install fvcore

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.8/44.8 kB 3.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 797.2/797.2 MB 1.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.0/7.0 MB 106.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 105.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 410.6/410.6 MB 1.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.1/14.1 MB 124.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.7/23.7 MB 102.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.6/823.6 kB 53.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 1.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.6/121.6 MB 7.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.5/56.5 MB 11.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 124.2/124.2 MB 7.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 19

In [ ]:
#@title Pull Latest Repo
from google.colab import userdata
from pathlib import Path

try:
  gh_token = userdata.get('vad_clip_gh_token')
except Exception:
  gh_token = None

REPO_NAME = "vad_clip_colab_notebook"
REPO_PATH = Path("/content") / REPO_NAME

if gh_token:
  GITHUB_URL = f"https://{gh_token}@github.com/hammad-ali1/{REPO_NAME}.git"
else:
  GITHUB_URL = f'https://github.com/hammad-ali1/{REPO_NAME}'

!rm -rf {REPO_PATH}
!git clone {GITHUB_URL}

!cp -r {REPO_PATH}/* /content

Cloning into 'vad_clip_colab_notebook'...
remote: Enumerating objects: 211, done.
remote: Counting objects: 100% (211/211), done.
remote: Compressing objects: 100% (133/133), done.
remote: Total 211 (delta 109), reused 154 (delta 74), pack-reused 0 (from 0)
Receiving objects: 100% (211/211), 1.78 MiB | 12.26 MiB/s, done.
Resolving deltas: 100% (109/109), done.


In [ ]:
!cd /content/vmamba/kernels/selective_scan && pip install .

Processing /content/vmamba/kernels/selective_scan
  Preparing metadata (setup.py) ... done
  Created wheel for selective_scan: filename=selective_scan-0.0.2-cp312-cp312-linux_x86_64.whl size=9293876 sha256=cb4a8d67547a02d8fd3458e2095cfb8f0e8df430c389b00029db9b81d666c397
  Stored in directory: /tmp/pip-ephem-wheel-cache-yrpq84p2/wheels/e0/f2/5a/bfc38021b58688bf7ba0131e4895249de8417294087d81d6bb
Successfully built selective_scan


In [ ]:
import torch
from torchvision.transforms import Compose, Resize, CenterCrop, ToTensor, Normalize

import os
import glob
from collections import OrderedDict

from models import CLIP_VMamba_S

import cv2
import numpy as np
from PIL import Image
from tqdm.auto import tqdm

/usr/local/lib/python3.12/dist-packages/timm/models/registry.py:4: FutureWarning: Importing from timm.models.registry is deprecated, please import via timm.models
  warnings.warn(f"Importing from {__name__} is deprecated, please import via timm.models", FutureWarning)
/usr/local/lib/python3.12/dist-packages/timm/models/layers/__init__.py:48: FutureWarning: Importing from timm.models.layers is deprecated, please import via timm.layers
  warnings.warn(f"Importing from {__name__} is deprecated, please import via timm.layers", FutureWarning)
/usr/local/lib/python3.12/dist-packages/mamba_ssm/ops/selective_scan_interface.py:163: FutureWarning: `torch.cuda.amp.custom_fwd(args...)` is deprecated. Please use `torch.amp.custom_fwd(args..., device_type='cuda')` instead.
  @custom_fwd
/usr/local/lib/python3.12/dist-packages/mamba_ssm/ops/selective_scan_interface.py:239: FutureWarning: `torch.cuda.amp.custom_bwd(args...)` is deprecated. Please use `torch.amp.custom_bwd(args..., device_type='cuda')`

In [ ]:
ZIPPED_DATASET = 'Anomaly-Videos-Part-1.zip'
EXTRACTED_DATASET = ZIPPED_DATASET.rstrip('.zip')
SAVE_DIR = '/content/drive/MyDrive/UCFMambaClipFeatures'
DATASET_URL = 'https://uce33f267412e87cce58446cf733.dl.dropboxusercontent.com/cd/0/get/CwAx4wYwmXou7TXOWKuWhCjiE2mRPyrqZt_B4ym8z1WkVQmhSVg0h5xEcF1nTDK-BXf5vLebBz0t3w8ZuZLwC3t3NJZyJOmjmmwXMaflA5kdqSAGOx-R-yQ8mj085Y9ZIO8NGx9Kyeooet3G3Ty-AaPtbPKy2DS9-eqWruj_P_Rgvw/file?_download_id=26268782287813734129726845317099701679539470673709982416201029642&_log_download_success=1&_notify_domain=www.dropbox.com&dl=1'


In [ ]:
!curl -L -o {ZIPPED_DATASET} {DATASET_URL}

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 5981M  100 5981M    0     0  51.1M      0  0:01:56  0:01:56 --:--:-- 41.0M


In [ ]:
!unzip -q {ZIPPED_DATASET}

In [ ]:
!cp -r /content/drive/MyDrive/Anomaly-Videos-Part-1 /content/Anomaly-Videos-Part-1

In [ ]:
def video_crop(video_frame, type):
    l = video_frame.shape[0]
    new_frame = []
    for i in range(l):
        img = cv2.resize(video_frame[i], dsize=(340, 256))
        new_frame.append(cv2.cvtColor(img, cv2.COLOR_BGR2RGB))

    #1
    img = np.array(new_frame)
    if type == 0:
        img = img[:, 16:240, 58:282, :]
    #2
    elif type == 1:
        img = img[:, :224, :224, :]
    #3
    elif type == 2:
        img = img[:, :224, -224:, :]
    #4
    elif type == 3:
        img = img[:, -224:, :224, :]
    #5
    elif type == 4:
        img = img[:, -224:, -224:, :]
    #6
    elif type == 5:
        img = img[:, 16:240, 58:282, :]
        for i in range(img.shape[0]):
            img[i] = cv2.flip(img[i], 1)
    #7
    elif type == 6:
        img = img[:, :224, :224, :]
        for i in range(img.shape[0]):
            img[i] = cv2.flip(img[i], 1)
    #8
    elif type == 7:
        img = img[:, :224, -224:, :]
        for i in range(img.shape[0]):
            img[i] = cv2.flip(img[i], 1)
    #9
    elif type == 8:
        img = img[:, -224:, :224, :]
        for i in range(img.shape[0]):
            img[i] = cv2.flip(img[i], 1)
    #10
    elif type == 9:
        img = img[:, -224:, -224:, :]
        for i in range(img.shape[0]):
            img[i] = cv2.flip(img[i], 1)

    return img

def image_crop(image, type):
    img = cv2.resize(image, dsize=(340, 256))
    img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
    #1
    if type == 0:
        img = img[16:240, 58:282, :]
    #2
    elif type == 1:
        img = img[:224, :224, :]
    #3
    elif type == 2:
        img = img[:224, -224:, :]
    #4
    elif type == 3:
        img = img[-224:, :224, :]
    #5
    elif type == 4:
        img = img[-224:, -224:, :]
    #6
    elif type == 5:
        img = img[16:240, 58:282, :]
        img = cv2.flip(img, 1)
    #7
    elif type == 6:
        img = img[:224, :224, :]
        img = cv2.flip(img, 1)
    #8
    elif type == 7:
        img = img[:224, -224:, :]
        img = cv2.flip(img, 1)
    #9
    elif type == 8:
        img = img[-224:, :224, :]
        img = cv2.flip(img, 1)
    #10
    elif type == 9:
        img = img[-224:, -224:, :]
        img = cv2.flip(img, 1)

    return img

In [ ]:
def _sample_frames_nonoverlap(video_path, stride=16, pick='center'):
    """
    Return one frame per non-overlapping `stride`-frame chunk.
    pick: 'center' | 'first' | 'last'
    - For stride=16, 'center' -> index 7 (0-based) so you'll get floor(T/16) frames.
    """
    assert stride >= 1
    cap = cv2.VideoCapture(video_path)
    sampled = []
    chunk = []
    center_idx = (stride // 2 - 1) if (stride % 2 == 0) else (stride // 2)

    while True:
        ret, frame = cap.read()
        if not ret:
            break
        chunk.append(frame)
        if len(chunk) == stride:
            if pick == 'center':
                idx = center_idx
            elif pick == 'first':
                idx = 0
            elif pick == 'last':
                idx = stride - 1
            else:
                raise ValueError(f"Unknown pick='{pick}'")
            sampled.append(chunk[idx])
            chunk.clear()

    cap.release()
    if len(sampled) == 0:
        return np.empty((0,), dtype=object)
    return np.array(sampled)  # shape: (floor(T/stride), H, W, C)

def extract_clip_features(video_path, save_dir, model, preprocess, device,
                          stride=16, pick='center'):
    """
    Extract CLIP features for all 10 crop types from a video using 1-of-`stride`
    non-overlapping sampling (paper style). Defaults: stride=16, pick='center'.
    """
    # --- prepare output paths ---
    video_name = os.path.splitext(os.path.basename(video_path))[0]
    parent_dir = os.path.basename(os.path.dirname(video_path))
    out_parent = os.path.join(save_dir, parent_dir)
    os.makedirs(out_parent, exist_ok=True)

    # --- skip if all crops exist ---
    if all(os.path.exists(os.path.join(out_parent, f"{video_name}__{c}.npy")) for c in range(10)):
        return

    # --- sample frames exactly floor(T/stride) ---
    frames = _sample_frames_nonoverlap(video_path, stride=stride, pick=pick)
    if frames.size == 0:
        raise ValueError(f"No frames found (after sampling) in {video_path}")

    for crop_type in tqdm(range(10),
                          desc=f"Video: {video_name}",
                          unit="crop",
                          position=1,
                          leave=False,
                          dynamic_ncols=True):
        save_path = os.path.join(out_parent, f"{video_name}__{crop_type}.npy")
        if os.path.exists(save_path):
            continue

        cropped_frames = video_crop(frames, crop_type)  # expects (N, H, W, C)

        video_features = []
        # inner frame bar: manual update so we fully control one line in-place
        pbar = tqdm(total=len(cropped_frames),
                    desc=f"Crop {crop_type}",
                    unit="frame",
                    position=2,
                    leave=False,
                    dynamic_ncols=True)
        with torch.no_grad():
            for f in cropped_frames:
                img = Image.fromarray(f)
                img = preprocess(img).unsqueeze(0).to(device)
                feat = model.encode_image(img)
                video_features.append(feat.cpu().numpy())
                pbar.update(1)
        pbar.close()

        video_features = np.vstack(video_features)  # shape: (floor(T/stride), 512)
        np.save(save_path, video_features)


In [ ]:
def extract_dataset_features(dataset_dir, save_dir, model, preprocess, device):
    # find all mp4 files recursively
    video_files = glob.glob(os.path.join(dataset_dir, "**", "*.mp4"), recursive=True)
    video_files.sort()  # stable ordering

    print(f"Found {len(video_files)} videos in {dataset_dir}")

    for video_path in tqdm(video_files, desc="Dataset", unit="video", position=0):
        try:
            extract_clip_features(
                video_path=video_path,
                save_dir=save_dir,
                model=model,
                preprocess=preprocess,
                device=device
            )
        except Exception as e:
            print(f"⚠️ Error processing {video_path}: {e}")


In [ ]:
def load_clip_model():
  !curl -L -o VMamba_S_clip.pt "https://huggingface.co/weiquan/mamba-clip/resolve/main/VMamba_S_clip.pt?download=true"

  mamba_clip_model = CLIP_VMamba_S()

  ckpt_path = "VMamba_S_clip.pt"

  ckpt = torch.load(ckpt_path, map_location='cpu', weights_only=False)
  state_dict = OrderedDict()
  for k, v in ckpt['state_dict'].items():
      state_dict[k.replace('module.', '')] = v

  mamba_clip_model.load_state_dict(state_dict, strict=True)

  return mamba_clip_model

In [ ]:
try:
    from torchvision.transforms import InterpolationMode
    BICUBIC = InterpolationMode.BICUBIC
except ImportError:
    BICUBIC = Image.BICUBIC

In [ ]:
def _convert_image_to_rgb(image):
    return image.convert("RGB")

def _transform(n_px=224):
    return Compose([
        Resize(n_px, interpolation=BICUBIC),
        CenterCrop(n_px),
        _convert_image_to_rgb,
        ToTensor(),
        Normalize((0.48145466, 0.4578275, 0.40821073), (0.26862954, 0.26130258, 0.27577711)),
    ])

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"
model = load_clip_model()
model = model.to(device)

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  1317  100  1317    0     0   6088      0 --:--:-- --:--:-- --:--:--  6097
100 1728M  100 1728M    0     0  69.5M      0  0:00:24  0:00:24 --:--:-- 70.1M


/content/vmamba/vmamba.py:262: FutureWarning: `torch.cuda.amp.custom_fwd(args...)` is deprecated. Please use `torch.amp.custom_fwd(args..., device_type='cuda')` instead.
  @torch.cuda.amp.custom_fwd
/content/vmamba/vmamba.py:270: FutureWarning: `torch.cuda.amp.custom_bwd(args...)` is deprecated. Please use `torch.amp.custom_bwd(args..., device_type='cuda')` instead.
  @torch.cuda.amp.custom_bwd
/content/vmamba/vmamba.py:285: FutureWarning: `torch.cuda.amp.custom_fwd(args...)` is deprecated. Please use `torch.amp.custom_fwd(args..., device_type='cuda')` instead.
  @torch.cuda.amp.custom_fwd
/content/vmamba/vmamba.py:293: FutureWarning: `torch.cuda.amp.custom_bwd(args...)` is deprecated. Please use `torch.amp.custom_bwd(args..., device_type='cuda')` instead.
  @torch.cuda.amp.custom_bwd
/content/vmamba/vmamba.py:306: FutureWarning: `torch.cuda.amp.custom_fwd(args...)` is deprecated. Please use `torch.amp.custom_fwd(args..., device_type='cuda')` instead.
  @torch.cuda.amp.custom_fwd
/cont

=> merge config from /content/vmamba/configs/vssm1/vssm_small_224.yaml


In [ ]:
preprocess = _transform()

In [ ]:
# extract_clip_features('/content/drive/MyDrive/Anomaly-Videos-Part-1/Abuse/Abuse001_x264.mp4', 'UCFMambaClipFeatures', model, preprocess, device)

Video: Abuse001_x264:   0%|          | 0/10 [00:00<?, ?crop/s]

Crop 0:   0%|          | 0/170 [00:00<?, ?frame/s]

/usr/local/lib/python3.12/dist-packages/torch/_dynamo/eval_frame.py:600: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.4 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  return fn(*args, **kwargs)
/usr/local/lib/python3.12/dist-packages/torch/utils/checkpoint.py:92: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn(


Crop 1:   0%|          | 0/170 [00:00<?, ?frame/s]

Crop 2:   0%|          | 0/170 [00:00<?, ?frame/s]

...

Crop 5:   0%|          | 0/170 [00:00<?, ?frame/s]

Crop 6:   0%|          | 0/170 [00:00<?, ?frame/s]

Crop 7:   0%|          | 0/170 [00:00<?, ?frame/s]

Crop 8:   0%|          | 0/170 [00:00<?, ?frame/s]

Crop 9:   0%|          | 0/170 [00:00<?, ?frame/s]

In [ ]:
processed_files = len(glob.glob(os.path.join(SAVE_DIR, "**", "*.npy"), recursive=True)) // 10
print(f'Already processed files: {processed_files}')

In [ ]:
extract_dataset_features(EXTRACTED_DATASET, SAVE_DIR, model, preprocess, device)

Found 200 videos in Anomaly-Videos-Part-1


Dataset:   0%|          | 0/200 [00:00<?, ?video/s]

Video: Arson019_x264:   0%|          | 0/10 [00:00<?, ?crop/s]

Crop 4:   0%|          | 0/7909 [00:00<?, ?frame/s]

/usr/local/lib/python3.12/dist-packages/torch/_dynamo/eval_frame.py:600: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.4 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  return fn(*args, **kwargs)
/usr/local/lib/python3.12/dist-packages/torch/utils/checkpoint.py:92: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn(


...

Crop 0:   0%|          | 0/434 [00:00<?, ?frame/s]

Crop 1:   0%|          | 0/434 [00:00<?, ?frame/s]

Crop 2:   0%|          | 0/434 [00:00<?, ?frame/s]

Crop 3:   0%|          | 0/434 [00:00<?, ?frame/s]

Crop 4:   0%|          | 0/434 [00:00<?, ?frame/s]